In [1]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [2]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [3]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/FinancialProgressReport/finProgress_newRpt.aspx"
params = {
    'params': 0
}
for key, value in params.items():
    url = url #+ "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [4]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddl_finYear'
radio_name = 'ctl00$ContentPlaceHolder1$rdlScheme'
subscheme_select_name = 'ctl00$ContentPlaceHolder1$ddlsp'
excel_button = 'ctl00$ContentPlaceHolder1$btnExport'
content_table_class = 'table_s'

In [5]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

def check_table():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.CSS_SELECTOR, '.'+content_table_class))            
    WebDriverWait(driver, 2).until(element_present)
    
#Check Submit button
def delete_excel():
    driver.execute_script("return document.getElementsByName('" + excel_button + "')[0].remove()")
def check_excel():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, excel_button ) ) )

In [6]:
#Start Chrome
driver.get(url)
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[-1:]
print(yearlist)
for year in yearlist:
    print("--Scrapping data for Year: ", year['text'])
    
    #Start Chrome
    driver.get(url)
    
    #DataStore
    df_list = []
    
    def select_year_scheme():
        #Year Selection
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, year_select_name))
        )
        element.find_element_by_xpath(".//option[@value='0']").click()
        year_query = ".//option[@value='" + year['value'] + "']"
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, year_select_name))
        )
        element.find_element_by_xpath(year_query).click()


        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, radio_name))
        )
        driver.find_elements_by_name(radio_name)[-3].click()
    
    select_year_scheme();
    
    #Find SubSchemes
    element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, subscheme_select_name))
    )
    element.find_element_by_xpath(".//option[@value='Select sub Scheme']").click()
    subschemelist = build_list(subscheme_select_name)#[1:4]
    for subscheme in subschemelist:
        print("--Scrapping data for SubScheme: ", subscheme['text'])
        
        #Start Chrome
        driver.get(url)
        select_year_scheme();
        
        #Select SubScheme
        element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, subscheme_select_name))
        )
        element.find_element_by_xpath(".//option[@value='Select sub Scheme']").click()
        
        scheme_query = ".//option[@value='" + subscheme['value'] + "']"
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, subscheme_select_name))
        )
        element.find_element_by_xpath(scheme_query).click()
        
        #state select
        check_table()
        temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[3:-2]
        states = []
        for row in temp_list:
            try:
                x = {}
                td = row.find_elements_by_xpath(".//td")[1]
                x['name'] = td.text
                x['link'] = td.find_element_by_tag_name("a").get_attribute("href")
                states.append(x)
            except Exception as e:
                print("Error while parsing table data |", e)
        for state in states:
            print("----Scrapping data for State: ", state['name'])
            driver.get(state['link'])
            check_table()
            temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
            districts = []
            for row in temp_list:
                x = {}            
                x['name'] = row.find_elements_by_xpath(".//td")[1].text
                x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
                districts.append(x)
            for district in districts:
                print("------Scrapping data for District: ", district['name'])
                driver.get(district['link'])
                check_table()
                temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
                blocks = []
                for row in temp_list:
                    x = {}            
                    x['name'] = row.find_elements_by_xpath(".//td")[1].text
                    x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
                    blocks.append(x)

                for block in blocks:
                    print("--------Scrapping data for Block: ", block['name'])
                    driver.get(block['link'])
                    check_table()
                    html_table = driver.find_element_by_class_name(content_table_class).get_attribute('outerHTML')
                    df = pd.read_html(html_table, header=3)[0]
                    df = df[:-1]
                    #df.columns = table_head
                    df['Financial Year'] = year['text']
                    df['State Name'] = state['name']
                    df['District Name'] = district['name']
                    df['Block Name'] = block['name']
                    df['Scheme'] = "All Central Scheme"
                    df['subscheme'] = subscheme['text']
                    df_list.append(df)
                    #except Exception as e:
                    #    print("Error while table data |", e)

    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df.drop(df.columns[0],axis=1,inplace=True)
    df = df.reset_index()
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'Special_Package_Scrapped_Data.csv'), encoding='utf-8', index=False)

[{'text': '2018-2019', 'value': '2018-2019 '}]
--Scrapping data for Year:  2018-2019
--Scrapping data for SubScheme:  Additional Houses
Error while parsing table data | Message: no such element: Unable to locate element: {"method":"tag name","selector":"a"}
  (Session info: chrome=67.0.3396.79)
  (Driver info: chromedriver=2.35.528161 (5b82f2d2aae0ca24b877009200ced9065a772e73),platform=Windows NT 10.0.17134 x86_64)

----Scrapping data for State:  ARUNACHAL PRADESH
----Scrapping data for State:  ASSAM
----Scrapping data for State:  BIHAR
----Scrapping data for State:  CHHATTISGARH
----Scrapping data for State:  GOA
----Scrapping data for State:  GUJARAT
----Scrapping data for State:  HARYANA
----Scrapping data for State:  HIMACHAL PRADESH
----Scrapping data for State:  JAMMU AND KASHMIR
----Scrapping data for State:  JHARKHAND
----Scrapping data for State:  KERALA
----Scrapping data for State:  MADHYA PRADESH
----Scrapping data for State:  MAHARASHTRA
----Scrapping data for State:  MANI

----Scrapping data for State:  GOA
----Scrapping data for State:  GUJARAT
----Scrapping data for State:  HARYANA
----Scrapping data for State:  HIMACHAL PRADESH
----Scrapping data for State:  JAMMU AND KASHMIR
----Scrapping data for State:  JHARKHAND
----Scrapping data for State:  KERALA
----Scrapping data for State:  MADHYA PRADESH
----Scrapping data for State:  MAHARASHTRA
----Scrapping data for State:  MANIPUR
----Scrapping data for State:  MEGHALAYA
----Scrapping data for State:  MIZORAM
----Scrapping data for State:  NAGALAND
----Scrapping data for State:  ODISHA
----Scrapping data for State:  PUNJAB
----Scrapping data for State:  RAJASTHAN
----Scrapping data for State:  SIKKIM
----Scrapping data for State:  TAMIL NADU
----Scrapping data for State:  TRIPURA
----Scrapping data for State:  UTTAR PRADESH
----Scrapping data for State:  UTTARAKHAND
----Scrapping data for State:  WEST BENGAL
----Scrapping data for State:  ANDAMAN AND NICOBAR
----Scrapping data for State:  DADRA AND NAGA

--------Scrapping data for Block:  ARAVAKURICHI
--------Scrapping data for Block:  K.PARAMATHI
--------Scrapping data for Block:  KADAVUR
--------Scrapping data for Block:  KARUR
--------Scrapping data for Block:  KRISHNARAYAPURAM
--------Scrapping data for Block:  KULITHALAI
--------Scrapping data for Block:  THANTHONI
--------Scrapping data for Block:  THOGAMALAI
------Scrapping data for District:  KRISHNAGIRI
--------Scrapping data for Block:  BARGUR
--------Scrapping data for Block:  HOSUR
--------Scrapping data for Block:  KAVERIPATTANAM
--------Scrapping data for Block:  KELAMANGALAM
--------Scrapping data for Block:  KRISHNAGIRI
--------Scrapping data for Block:  MATHUR
--------Scrapping data for Block:  SHOOLAGIRI
--------Scrapping data for Block:  THALLY
--------Scrapping data for Block:  UTHANGARAI
--------Scrapping data for Block:  VEPPANAPALLI
------Scrapping data for District:  MADURAI
--------Scrapping data for Block:  ALANGANALLUR
--------Scrapping data for Block:  KALLI

--------Scrapping data for Block:  KURUVIKULAM
--------Scrapping data for Block:  MANUR
--------Scrapping data for Block:  MELANEELITHANALLUR
--------Scrapping data for Block:  NANGUNERI
--------Scrapping data for Block:  PALAYAMKOTTAI
--------Scrapping data for Block:  PAPPAKUDI
--------Scrapping data for Block:  SANKARANKOIL
--------Scrapping data for Block:  SHENCOTTAI
--------Scrapping data for Block:  TENKASI
--------Scrapping data for Block:  VASUDEVANALLUR
------Scrapping data for District:  TIRUPPUR
--------Scrapping data for Block:  AVINASHI
--------Scrapping data for Block:  DHARAPURAM
--------Scrapping data for Block:  GUDIMANGALAM
--------Scrapping data for Block:  KANGAYAM
--------Scrapping data for Block:  KUNDADAM
--------Scrapping data for Block:  MADATHUKULAM
--------Scrapping data for Block:  MULANUR
--------Scrapping data for Block:  PALLADAM
--------Scrapping data for Block:  TIRUPPUR
--------Scrapping data for Block:  UDUMALPET
--------Scrapping data for Block:  UT

------Scrapping data for District:  SURGUJA
--------Scrapping data for Block:  AMBIKAPUR
--------Scrapping data for Block:  BATAULI
--------Scrapping data for Block:  LUNDRA
--------Scrapping data for Block:  MAINPAT
----Scrapping data for State:  GOA
----Scrapping data for State:  GUJARAT
----Scrapping data for State:  HARYANA
----Scrapping data for State:  HIMACHAL PRADESH
----Scrapping data for State:  JAMMU AND KASHMIR
----Scrapping data for State:  JHARKHAND
----Scrapping data for State:  KERALA
----Scrapping data for State:  MADHYA PRADESH
------Scrapping data for District:  BALAGHAT
--------Scrapping data for Block:  BIRSA
--------Scrapping data for Block:  KIRNAPUR
------Scrapping data for District:  BARWANI
--------Scrapping data for Block:  SENDHAWA
------Scrapping data for District:  BETUL
--------Scrapping data for Block:  CHICHOLI
------Scrapping data for District:  DAMOH
--------Scrapping data for Block:  TENDUKHEDA
------Scrapping data for District:  DEWAS
--------Scrapp

--------Scrapping data for Block:  Jaora
------Scrapping data for District:  SATNA
--------Scrapping data for Block:  MAJHGAWAN
--------Scrapping data for Block:  RAMPUR BAGHELAN
--------Scrapping data for Block:  Satna
------Scrapping data for District:  SEHORE
--------Scrapping data for Block:  Sehore
------Scrapping data for District:  SHAHDOL
--------Scrapping data for Block:  JAISINGHNAGAR
------Scrapping data for District:  SHEOPUR
--------Scrapping data for Block:  Sheopur
------Scrapping data for District:  SHIVPURI
--------Scrapping data for Block:  KHANIYADHANA
------Scrapping data for District:  SIDHI
--------Scrapping data for Block:  KUSMI
--------Scrapping data for Block:  RAMPUR NAIKIN
--------Scrapping data for Block:  SIHAWAL
------Scrapping data for District:  TIKAMGARH
--------Scrapping data for Block:  BALDEOGARH
--------Scrapping data for Block:  NIWARI
--------Scrapping data for Block:  PALERA
----Scrapping data for State:  MAHARASHTRA
----Scrapping data for State

----Scrapping data for State:  ASSAM
----Scrapping data for State:  BIHAR
----Scrapping data for State:  CHHATTISGARH
----Scrapping data for State:  GOA
----Scrapping data for State:  GUJARAT
----Scrapping data for State:  HARYANA
----Scrapping data for State:  HIMACHAL PRADESH
----Scrapping data for State:  JAMMU AND KASHMIR
----Scrapping data for State:  JHARKHAND
----Scrapping data for State:  KERALA
----Scrapping data for State:  MADHYA PRADESH
----Scrapping data for State:  MAHARASHTRA
----Scrapping data for State:  MANIPUR
----Scrapping data for State:  MEGHALAYA
----Scrapping data for State:  MIZORAM
----Scrapping data for State:  NAGALAND
----Scrapping data for State:  ODISHA
----Scrapping data for State:  PUNJAB
----Scrapping data for State:  RAJASTHAN
----Scrapping data for State:  SIKKIM
----Scrapping data for State:  TAMIL NADU
----Scrapping data for State:  TRIPURA
----Scrapping data for State:  UTTAR PRADESH
----Scrapping data for State:  UTTARAKHAND
----Scrapping data fo

----Scrapping data for State:  ANDAMAN AND NICOBAR
----Scrapping data for State:  DADRA AND NAGAR HAVELI
----Scrapping data for State:  DAMAN AND DIU
----Scrapping data for State:  LAKSHADWEEP
----Scrapping data for State:  PUDUCHERRY
----Scrapping data for State:  ANDHRA PRADESH
----Scrapping data for State:  KARNATAKA
----Scrapping data for State:  TELANGANA
--Scrapping data for SubScheme:  Rehabilitation of surrendered militants
Error while parsing table data | Message: no such element: Unable to locate element: {"method":"tag name","selector":"a"}
  (Session info: chrome=67.0.3396.79)
  (Driver info: chromedriver=2.35.528161 (5b82f2d2aae0ca24b877009200ced9065a772e73),platform=Windows NT 10.0.17134 x86_64)

----Scrapping data for State:  ARUNACHAL PRADESH
----Scrapping data for State:  ASSAM
----Scrapping data for State:  BIHAR
----Scrapping data for State:  CHHATTISGARH
----Scrapping data for State:  GOA
----Scrapping data for State:  GUJARAT
----Scrapping data for State:  HARYANA


----Scrapping data for State:  KERALA
----Scrapping data for State:  MADHYA PRADESH
----Scrapping data for State:  MAHARASHTRA
----Scrapping data for State:  MANIPUR
----Scrapping data for State:  MEGHALAYA
----Scrapping data for State:  MIZORAM
----Scrapping data for State:  NAGALAND
----Scrapping data for State:  ODISHA
----Scrapping data for State:  PUNJAB
----Scrapping data for State:  RAJASTHAN
----Scrapping data for State:  SIKKIM
----Scrapping data for State:  TAMIL NADU
----Scrapping data for State:  TRIPURA
----Scrapping data for State:  UTTAR PRADESH
----Scrapping data for State:  UTTARAKHAND
----Scrapping data for State:  WEST BENGAL
----Scrapping data for State:  ANDAMAN AND NICOBAR
----Scrapping data for State:  DADRA AND NAGAR HAVELI
----Scrapping data for State:  DAMAN AND DIU
----Scrapping data for State:  LAKSHADWEEP
----Scrapping data for State:  PUDUCHERRY
----Scrapping data for State:  ANDHRA PRADESH
----Scrapping data for State:  KARNATAKA
----Scrapping data for St